In [15]:
import sys
sys.path.append("..")
sys.path.append("/home/lizian/Self-Conditioned-3D-Diffusion")
import os
os.chdir("/home/lizian/Self-Conditioned-3D-Diffusion")

from omegaconf import OmegaConf
import torch
from qm9 import dataset
from configs.datasets_config import get_dataset_info
device = "cuda:2"
from pathlib import Path

seed = 0
torch.manual_seed(seed)
torch.cuda.manual_seed(seed)
torch.cuda.manual_seed_all(seed)  # if using multi-GPU
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = False

In [16]:
# Intialize dataset config for **unconditional qm9**
dataset_args = {
    "dataset": "qm9",
    "conditioning": [],
    "include_charges": True,
    "world_size": 1,
    "rank": 0,
    "filter_n_atoms": None,
    "remove_h": False,
    "batch_size": 128,
    "num_workers": 4,
    "datadir": "./data"
}
vis_num_atom = 19
show_num = 500
images_per_row = 5
dtype = torch.float32
id_from = 0

In [17]:
# Init dataset, dataloaderes and property samplers
dataset_args = OmegaConf.create(dataset_args)
datasets, collate_fn = dataset.retrieve_dataloaders(dataset_args, return_raw_datasets_and_collate_fn=True)
train_dataset = datasets["train"]
# train_dataset.perm = torch.arange(len(train_dataset), dtype=torch.int)
num_atoms = train_dataset.data["num_atoms"]
dataset_info = get_dataset_info(dataset_args.dataset, dataset_args.remove_h)
train_dataset.perm = torch.arange(0, len(train_dataset))

In [18]:
# Get ready-to-show datas
mask = num_atoms == vis_num_atom
idx = mask.nonzero().flatten()
data_list = []
for i in idx:
    data_list.append(train_dataset[i])
data_list = data_list[:show_num]
datas = collate_fn(data_list)
datas["index"]

tensor([ 1084,  1088,  1093,  1107,  1120,  1133,  1142,  1146,  1149,  1174,
         1187,  1193,  1197,  1239,  1268,  1275,  1292,  1293,  1300,  1312,
         1316,  1317,  1318,  1333,  1338,  1339,  1341,  1343,  1346,  1352,
         1355,  1360,  1361,  1465,  1470,  1513,  1557,  1568,  1569,  1574,
         1578,  1579,  1658,  1673,  1688,  1696,  1717,  1722,  1723,  1725,
         1747,  1750,  1751,  1752,  1784,  1789,  1791,  1795,  1808,  1809,
         1810,  1816,  1857,  1862,  1892,  1897,  1914,  1923,  1929,  1972,
         1975,  1976,  1996,  1998,  2012,  2026,  2034,  2043,  2047,  2086,
         2103,  2104,  2105,  2110,  2148,  2153,  2174,  2176,  2205,  2206,
         2208,  2220,  2237,  2265,  2292,  2296,  2299,  2330,  2335,  2337,
         2339,  2342,  2360,  2361,  2367,  2369,  2387,  2392,  2441,  2464,
         2481,  2528,  2542,  2551,  2552,  2575,  2576,  2679,  2706,  2725,
         2726,  2727,  2728,  2729,  2730,  2795,  2799,  2800, 

In [19]:
from qm9 import visualizer as qm9_visualizer

one_hot, x, node_mask, charges = datas["one_hot"].to(dtype), datas["positions"].to(dtype), datas["atom_mask"].to(dtype), None
target_path = Path(f"/home/lizian/Self-Conditioned-3D-Diffusion/visualize_results/qm9/qm9_{vis_num_atom}/")



if target_path.exist():
    assert 0, "Please delete existing files to avoid potential bugs."

qm9_visualizer.save_xyz_file(
target_path, one_hot, charges, x,
dataset_info, id_from, name=f'qm9_{vis_num_atom}', node_mask=node_mask)

qm9_visualizer.visualize(
target_path, dataset_info,
spheres_3d=True, max_num=show_num, show_Hs=False)

Average distance between atoms 3.036670684814453
Average distance between atoms 3.318005323410034
Average distance between atoms 3.067216157913208
Average distance between atoms 3.161804437637329
Average distance between atoms 3.000239849090576
Average distance between atoms 3.0775864124298096
Average distance between atoms 3.494763135910034
Average distance between atoms 3.064196825027466
Average distance between atoms 3.2076609134674072
Average distance between atoms 3.0754623413085938
Average distance between atoms 3.103193998336792
Average distance between atoms 3.172722816467285
Average distance between atoms 3.6764473915100098
Average distance between atoms 3.1213736534118652
Average distance between atoms 3.5176398754119873
Average distance between atoms 3.5788753032684326
Average distance between atoms 3.448439598083496
Average distance between atoms 3.3397088050842285
Average distance between atoms 3.5593111515045166
Average distance between atoms 3.4661478996276855
Average di

In [20]:
vis_num_atom

19

In [21]:
import matplotlib.pyplot as plt
import matplotlib.image as mpimg

image_list = []
for i in range(show_num):
    image_path = target_path / f"qm9_{vis_num_atom}_%03d.png"% (i)
    image_list.append(image_path)

# Calculate the number of rows needed
num_rows = len(image_list) // images_per_row + int(len(image_list) % images_per_row != 0)

# Create a figure
fig, axes = plt.subplots(num_rows, images_per_row, figsize=(30, 3 * num_rows))

# Iterate over the images and plot them
for idx, image_path in enumerate(image_list):
    try:
        img = mpimg.imread(image_path)
    except:
        print(f"No {image_path}")
        import numpy as np
        img = np.ones((100, 100, 3))
    row = idx // images_per_row
    col = idx % images_per_row
    axes[row, col].imshow(img)
    axes[row, col].axis('off')  # Hide the axis
    # Add the index below the image
    axes[row, col].text(0.5, -0.05, f"Index: {datas['index'][idx]}", ha='center', va='center', transform=axes[row, col].transAxes)

# Remove any empty subplots
for idx in range(len(image_list), num_rows * images_per_row):
    row = idx // images_per_row
    col = idx % images_per_row
    axes[row, col].axis('off')

# Show the plot
plt.tight_layout()
%matplotlib inline
plt.show()